In [1]:
#-*-coding:utf-8-*-
import util
import tensorflow as tf
MNIST_CLASSIFIER_FROZEN_GRAPH = './classify_mnist_graph_def.pb'
INPUT_TENSOR = 'inputs:0'
OUTPUT_TENSOR = 'logits:0'
def EuclideanDistances(A, B):

    BT = B.transpose()
    # vecProd = A * BT
    vecProd = np.dot(A, BT)
    # print(vecProd)
    SqA = A ** 2
    # print(SqA)
    sumSqA = np.matrix(np.sum(SqA, axis=1))
    sumSqAEx = np.tile(sumSqA.transpose(), (1, vecProd.shape[1]))
    # print(sumSqAEx)

    SqB = B ** 2
    sumSqB = np.sum(SqB, axis=1)
    sumSqBEx = np.tile(sumSqB, (vecProd.shape[0], 1))
    SqED = sumSqBEx + sumSqAEx - 2 * vecProd
    SqED[SqED < 0] = 0.0
    ED = np.sqrt(SqED)
    return np.divide(ED.sum(),ED.shape[0]*ED.shape[1])
def cal_distance_image_real(images,labels):
    eval_images=tf.convert_to_tensor(images)
    y_logits=util.mnist_logits(eval_images, MNIST_CLASSIFIER_FROZEN_GRAPH, INPUT_TENSOR, OUTPUT_TENSOR)
    y_logits=tf.Session().run(y_logits)
    dict={}
    all_dis=[]
    for i in range(10):
        dict[i]=[]
    for i in range(len(labels)):
        dict[labels[i]].append(y_logits[i])
    for i in range(10):
        dict[i]=np.array(dict[i])
        if len(dict[i]):
            dis = EuclideanDistances(dict[i], dict[i])  # 生成图片的紧度
        else:
            dis = -1
        all_dis.append(dis)
    return np.array(all_dis)
def cal_distance_image_fake(images):
    eval_images=tf.convert_to_tensor(images)
    y_logits=util.mnist_logits(eval_images, MNIST_CLASSIFIER_FROZEN_GRAPH, INPUT_TENSOR, OUTPUT_TENSOR)
    y_logits=tf.Session().run(y_logits)
    labels = tf.Session().run(tf.argmax(y_logits, 1))
    dict={}
    all_dis=[]
    for i in range(10):
        dict[i]=[]
    for i in range(len(labels)):
        dict[labels[i]].append(y_logits[i])
    for i in range(10):
        dict[i]=np.array(dict[i])
        if len(dict[i]):
            dis = EuclideanDistances(dict[i], dict[i])  # 生成图片的紧度
        else:
            dis = -1
        all_dis.append(dis)
    return np.array(all_dis)

    

In [2]:
import os
if not os.path.isdir('saved_models_{}'.format('wpgan')):
    os.mkdir('saved_models_{}'.format('wpgan'))
f = open('saved_models_{}/log_collapse1.txt'.format('wpgan'), mode='w')
import cv2


# Large amount of credit goes to:
# https://github.com/keras-team/keras-contrib/blob/master/examples/improved_wgan.py
# which I've used as a reference for this implementation



from keras.datasets import mnist,fashion_mnist
from keras.layers.merge import _Merge
from keras.layers import Input, Dense, Reshape, Flatten, Dropout
from keras.layers import BatchNormalization, Activation, ZeroPadding2D
from keras.layers.advanced_activations import LeakyReLU
from keras.layers.convolutional import UpSampling2D, Conv2D
from keras.models import Sequential, Model
from keras.optimizers import RMSprop
from functools import partial

import keras.backend as K

import matplotlib.pyplot as plt

import sys

import numpy as np
import os
class RandomWeightedAverage(_Merge):
    """Provides a (random) weighted average between real and generated image samples"""
    def _merge_function(self, inputs):
        alpha = K.random_uniform((32, 1, 1, 1))
        return (alpha * inputs[0]) + ((1 - alpha) * inputs[1])

class WGANGP():
    def __init__(self):
        self.img_rows = 28
        self.img_cols = 28
        self.channels = 1
        self.img_shape = (self.img_rows, self.img_cols, self.channels)
        self.latent_dim = 100
        self.x = []
        self.y = np.zeros((31, 1), dtype=np.int)
        self.y = list(self.y)
        for i in range(31):
            self.y[i] = []

        # Following parameter and optimizer set as recommended in paper
        self.n_critic = 5
        optimizer = RMSprop(lr=0.00005)

        # Build the generator and critic
        self.generator = self.build_generator()
        self.critic = self.build_critic()

        #-------------------------------
        # Construct Computational Graph
        #       for the Critic
        #-------------------------------

        # Freeze generator's layers while training critic
        self.generator.trainable = False

        # Image input (real sample)
        real_img = Input(shape=self.img_shape)

        # Noise input
        z_disc = Input(shape=(self.latent_dim,))
        # Generate image based of noise (fake sample)
        fake_img = self.generator(z_disc)

        # Discriminator determines validity of the real and fake images
        fake = self.critic(fake_img)
        valid = self.critic(real_img)

        # Construct weighted average between real and fake images
        interpolated_img = RandomWeightedAverage()([real_img, fake_img])
        # Determine validity of weighted sample
        validity_interpolated = self.critic(interpolated_img)

        # Use Python partial to provide loss function with additional
        # 'averaged_samples' argument
        partial_gp_loss = partial(self.gradient_penalty_loss,
                          averaged_samples=interpolated_img)
        partial_gp_loss.__name__ = 'gradient_penalty' # Keras requires function names

        self.critic_model = Model(inputs=[real_img, z_disc],
                            outputs=[valid, fake, validity_interpolated])
        self.critic_model.compile(loss=[self.wasserstein_loss,
                                              self.wasserstein_loss,
                                              partial_gp_loss],
                                        optimizer=optimizer,
                                        loss_weights=[1, 1, 10])
        #-------------------------------
        # Construct Computational Graph
        #         for Generator
        #-------------------------------

        # For the generator we freeze the critic's layers
        self.critic.trainable = False
        self.generator.trainable = True

        # Sampled noise for input to generator
        z_gen = Input(shape=(100,))
        # Generate images based of noise
        img = self.generator(z_gen)
        # Discriminator determines validity
        valid = self.critic(img)
        # Defines generator model
        self.generator_model = Model(z_gen, valid)
        self.generator_model.compile(loss=self.wasserstein_loss, optimizer=optimizer)


    def gradient_penalty_loss(self, y_true, y_pred, averaged_samples):
        """
        Computes gradient penalty based on prediction and weighted real / fake samples
        """
        gradients = K.gradients(y_pred, averaged_samples)[0]
        # compute the euclidean norm by squaring ...
        gradients_sqr = K.square(gradients)
        #   ... summing over the rows ...
        gradients_sqr_sum = K.sum(gradients_sqr,
                                  axis=np.arange(1, len(gradients_sqr.shape)))
        #   ... and sqrt
        gradient_l2_norm = K.sqrt(gradients_sqr_sum)
        # compute lambda * (1 - ||grad||)^2 still for each single sample
        gradient_penalty = K.square(1 - gradient_l2_norm)
        # return the mean as loss over all the batch samples
        return K.mean(gradient_penalty)


    def wasserstein_loss(self, y_true, y_pred):
        return K.mean(y_true * y_pred)

    def build_generator(self):

        model = Sequential()

        model.add(Dense(128 * 7 * 7, activation="relu", input_dim=self.latent_dim))
        model.add(Reshape((7, 7, 128)))
        model.add(UpSampling2D())
        model.add(Conv2D(128, kernel_size=4, padding="same"))
        model.add(BatchNormalization(momentum=0.8))
        model.add(Activation("relu"))
        model.add(UpSampling2D())
        model.add(Conv2D(64, kernel_size=4, padding="same"))
        model.add(BatchNormalization(momentum=0.8))
        model.add(Activation("relu"))
        model.add(Conv2D(self.channels, kernel_size=4, padding="same"))
        model.add(Activation("tanh"))

        model.summary()

        noise = Input(shape=(self.latent_dim,))
        img = model(noise)

        return Model(noise, img)

    def build_critic(self):

        model = Sequential()

        model.add(Conv2D(16, kernel_size=3, strides=2, input_shape=self.img_shape, padding="same"))
        model.add(LeakyReLU(alpha=0.2))
        model.add(Dropout(0.25))
        model.add(Conv2D(32, kernel_size=3, strides=2, padding="same"))
        model.add(ZeroPadding2D(padding=((0,1),(0,1))))
        model.add(BatchNormalization(momentum=0.8))
        model.add(LeakyReLU(alpha=0.2))
        model.add(Dropout(0.25))
        model.add(Conv2D(64, kernel_size=3, strides=2, padding="same"))
        model.add(BatchNormalization(momentum=0.8))
        model.add(LeakyReLU(alpha=0.2))
        model.add(Dropout(0.25))
        model.add(Conv2D(128, kernel_size=3, strides=1, padding="same"))
        model.add(BatchNormalization(momentum=0.8))
        model.add(LeakyReLU(alpha=0.2))
        model.add(Dropout(0.25))
        model.add(Flatten())
        model.add(Dense(1))

        model.summary()

        img = Input(shape=self.img_shape)
        validity = model(img)

        return Model(img, validity)

    def train(self, epochs, batch_size, sample_interval=50):

        # Load the dataset
        (X_train, _), (X_test, y_test) = fashion_mnist.load_data()

        # # Rescale -1 to 1
        # X_train = (X_train.astype(np.float32) - 127.5) / 127.5
        # X_train = np.expand_dims(X_train, axis=3)
        X_train = (X_train.astype(np.float32) - 127.5) / 127.5
        X_train = np.expand_dims(X_train, axis=3)
        X_test = (X_test.astype(np.float32) - 127.5) / 127.5
        X_test = np.expand_dims(X_test, axis=3)
        # y_train = y_train.reshape(-1, 1)

        # Adversarial ground truths
        valid = -np.ones((batch_size, 1))
        fake =  np.ones((batch_size, 1))
        dummy = np.zeros((batch_size, 1)) # Dummy gt for gradient penalty
        nb_batches = int(X_train.shape[0] / batch_size)
        global_step = 0

        for epoch in range(epochs):

            for index in range(nb_batches):
                for _ in range(self.n_critic):
                    global_step += 1
                    imgs = X_train[index * batch_size:(index + 1) * batch_size]
                    # Sample generator input
                    noise = np.random.normal(0, 1, (batch_size, self.latent_dim))
                    # Train the critic
                    d_loss = self.critic_model.train_on_batch([imgs, noise],
                                                              [valid, fake, dummy])

                    # ---------------------
                    #  Train Generator
                    # ---------------------

                g_loss = self.generator_model.train_on_batch(noise, valid)

                # Plot the progress
                print("epoch%d step%d [D loss: %f] [G loss: %f]" % (epoch, global_step, d_loss[0], g_loss))

                sampleSize = 5000
                # If at save interval => save generated image samples
                if global_step % sample_interval == 0:
                    s = self.sample_images(global_step, X_test,y_test, sampleSize)
    def sample_images(self, epoch,x_test,y_test,sample_num):
        r, c = sample_num//10, 10
        noise = np.random.normal(0, 1, (r * c, 100))
#         sampled_labels = np.array([num for _ in range(r) for num in range(c)])
        gen_imgs = self.generator.predict([noise])
        # Rescale images 0 - 1
        gen_imgs = 0.5 * gen_imgs + 0.5
        labels = np.squeeze(y_test[:sample_num])
        labels = np.squeeze(labels)
        dis_real = cal_distance_image_real(x_test[:sample_num], labels)
        dis_fake = cal_distance_image_fake(gen_imgs)
        dis_cha = dis_real - dis_fake
        print('##############')
        # print(dis_real)
        # print(dis_fake)
        print(dis_cha)
        print('##########')
        f.writelines('\n')
        f.writelines('epoch:' + str(epoch))
        f.writelines('\n')
        f.writelines('紧度')
        f.writelines('\n')
        f.writelines(' %.8f ' % (i) for i in dis_cha)
        f.writelines('\n')

#     def sample_images(self, epoch, sampleSize):
#         r, c = sampleSize // 10, 10
#         noise = np.random.normal(0, 1, (r * c, 100))
#         # sampled_labels = np.array([num for _ in range(r) for num in range(c)])
#         gen_imgs = self.generator.predict([noise])
#         # Rescale images 0 - 1
#         # gen_imgs = 0.5 * gen_imgs + 0.5
#         gen_imgs = 0.5 * gen_imgs + 0.5
#         labels = np.squeeze(y_test[:sampleSize])

#         inter_real = get_silhouette_score_real(X_test[:sampleSize], labels)  # 真实图片的紧度
#         inter_fake = get_silhouette_score_fake(gen_imgs)  # 生成图片的紧度
#         if type(inter_fake) == "<class 'int'>":
#             print('仅生成一种类型的图片')
#         else:
#             dist, chazhi = cal_mean_value(inter_real, inter_fake)  # 紧度的差值
#             print(chazhi)
#             print(dist)
#         f.writelines('\n')
#         f.writelines('epoch:' + str(epoch))
#         f.writelines('\n')
#         f.writelines('紧度')
#         f.writelines('\n')
#         f.writelines(' %.8f ' % (i) for i in chazhi)
#         f.writelines('\n')
#         f.writelines(str(dist))
#         f.writelines('\n')

if __name__ == '__main__':
    wgan = WGANGP()
    wgan.train(epochs=40, batch_size=32, sample_interval=200)


Using TensorFlow backend.


_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_1 (Dense)              (None, 6272)              633472    
_________________________________________________________________
reshape_1 (Reshape)          (None, 7, 7, 128)         0         
_________________________________________________________________
up_sampling2d_1 (UpSampling2 (None, 14, 14, 128)       0         
_________________________________________________________________
conv2d_1 (Conv2D)            (None, 14, 14, 128)       262272    
_________________________________________________________________
batch_normalization_1 (Batch (None, 14, 14, 128)       512       
_________________________________________________________________
activation_1 (Activation)    (None, 14, 14, 128)       0         
_________________________________________________________________
up_sampling2d_2 (UpSampling2 (None, 28, 28, 128)       0         
__________

/home/imi432_006/anaconda3/envs/tf/lib/python3.5/site-packages/keras/engine/training.py:490: UserWarning: Discrepancy between trainable weights and collected trainable weights, did you set `model.trainable` without calling `model.compile` after ?
  'Discrepancy between trainable weights and collected trainable'


epoch0 step5 [D loss: 36.099499] [G loss: -0.337049]
epoch0 step10 [D loss: 32.973698] [G loss: -0.456113]
epoch0 step15 [D loss: 27.606066] [G loss: -0.476376]
epoch0 step20 [D loss: 21.522738] [G loss: -0.168931]
epoch0 step25 [D loss: 19.537455] [G loss: -0.405950]
epoch0 step30 [D loss: 20.675964] [G loss: -0.577258]
epoch0 step35 [D loss: 17.371437] [G loss: -0.619349]
epoch0 step40 [D loss: 14.710247] [G loss: -0.291497]
epoch0 step45 [D loss: 17.527027] [G loss: -0.228010]
epoch0 step50 [D loss: 12.006821] [G loss: -0.405240]
epoch0 step55 [D loss: 11.414234] [G loss: -0.591514]
epoch0 step60 [D loss: 11.752393] [G loss: -0.446443]
epoch0 step65 [D loss: 9.756234] [G loss: -0.430900]
epoch0 step70 [D loss: 8.808109] [G loss: -0.534049]
epoch0 step75 [D loss: 8.143759] [G loss: -0.354265]
epoch0 step80 [D loss: 5.432536] [G loss: -0.281882]
epoch0 step85 [D loss: 3.671769] [G loss: -0.285210]
epoch0 step90 [D loss: 5.018019] [G loss: -0.148902]
epoch0 step95 [D loss: 3.633883] [G

epoch0 step700 [D loss: -1.456625] [G loss: 1.805437]
epoch0 step705 [D loss: -0.698573] [G loss: 1.800222]
epoch0 step710 [D loss: -0.545634] [G loss: 1.656166]
epoch0 step715 [D loss: -0.610654] [G loss: 1.415154]
epoch0 step720 [D loss: -0.747705] [G loss: 1.033434]
epoch0 step725 [D loss: -0.638448] [G loss: 0.790708]
epoch0 step730 [D loss: -0.721856] [G loss: 0.856624]
epoch0 step735 [D loss: -0.913623] [G loss: 0.968520]
epoch0 step740 [D loss: -1.343548] [G loss: 1.342600]
epoch0 step745 [D loss: -1.353667] [G loss: 0.964397]
epoch0 step750 [D loss: -1.585974] [G loss: 1.196152]
epoch0 step755 [D loss: -1.538519] [G loss: 1.134224]
epoch0 step760 [D loss: -1.313254] [G loss: 1.013495]
epoch0 step765 [D loss: -1.355145] [G loss: 0.851628]
epoch0 step770 [D loss: -1.249424] [G loss: 0.230635]
epoch0 step775 [D loss: -1.240211] [G loss: 0.390080]
epoch0 step780 [D loss: -0.787332] [G loss: 0.246969]
epoch0 step785 [D loss: -0.270499] [G loss: 0.320247]
epoch0 step790 [D loss: -0.3

...

epoch32 step300150 [D loss: -0.274291] [G loss: -5.760947]
epoch32 step300155 [D loss: 0.402690] [G loss: -4.926607]
epoch32 step300160 [D loss: 0.341210] [G loss: -5.408751]
epoch32 step300165 [D loss: 0.175625] [G loss: -5.384488]
epoch32 step300170 [D loss: -0.247674] [G loss: -5.988131]
epoch32 step300175 [D loss: -0.621495] [G loss: -4.779036]
epoch32 step300180 [D loss: -0.048210] [G loss: -4.938437]
epoch32 step300185 [D loss: -0.065979] [G loss: -5.642749]
epoch32 step300190 [D loss: -0.601626] [G loss: -5.382402]
epoch32 step300195 [D loss: -0.786158] [G loss: -4.972215]
epoch32 step300200 [D loss: -0.549352] [G loss: -5.416906]
##############
[2.6991272  2.27839769 1.70409955 2.79968007 0.50636328 6.19056882
 2.4998573  2.85392195 4.04544894 5.49214448]
##########
epoch32 step300205 [D loss: -0.332865] [G loss: -5.945693]
epoch32 step300210 [D loss: 0.468147] [G loss: -5.763865]
epoch32 step300215 [D loss: -0.946966] [G loss: -5.973248]
epoch32 step300220 [D loss: -0.023847] 

epoch32 step300810 [D loss: 0.042013] [G loss: -5.427908]
epoch32 step300815 [D loss: 0.898305] [G loss: -5.209364]
epoch32 step300820 [D loss: -0.073297] [G loss: -5.461591]
epoch32 step300825 [D loss: -0.914129] [G loss: -5.504236]
epoch32 step300830 [D loss: -0.216301] [G loss: -5.661576]
epoch32 step300835 [D loss: -0.992843] [G loss: -5.884806]
epoch32 step300840 [D loss: 0.134073] [G loss: -5.559507]
epoch32 step300845 [D loss: 0.397084] [G loss: -5.718934]
epoch32 step300850 [D loss: -0.289395] [G loss: -5.282578]
epoch32 step300855 [D loss: -0.020033] [G loss: -4.944596]
epoch32 step300860 [D loss: 0.257636] [G loss: -5.325249]
epoch32 step300865 [D loss: 0.147636] [G loss: -5.022854]
epoch32 step300870 [D loss: -0.177427] [G loss: -4.852869]
epoch32 step300875 [D loss: -0.577914] [G loss: -5.208288]
epoch32 step300880 [D loss: 0.353291] [G loss: -4.979497]
epoch32 step300885 [D loss: 0.123233] [G loss: -5.837711]
epoch32 step300890 [D loss: -1.342885] [G loss: -5.128826]
epoch

epoch32 step301480 [D loss: 0.266420] [G loss: -5.481505]
epoch32 step301485 [D loss: -0.123987] [G loss: -5.980476]
epoch32 step301490 [D loss: -0.417885] [G loss: -5.762257]
epoch32 step301495 [D loss: 0.593256] [G loss: -5.910779]
epoch32 step301500 [D loss: -0.735624] [G loss: -6.410399]
epoch32 step301505 [D loss: -0.391742] [G loss: -5.723534]
epoch32 step301510 [D loss: 0.003738] [G loss: -5.323008]
epoch32 step301515 [D loss: 0.018813] [G loss: -5.177272]
epoch32 step301520 [D loss: -0.534335] [G loss: -6.007344]
epoch32 step301525 [D loss: -0.474549] [G loss: -6.220935]
epoch32 step301530 [D loss: -0.547379] [G loss: -5.897009]
epoch32 step301535 [D loss: -0.317540] [G loss: -5.736091]
epoch32 step301540 [D loss: 0.169399] [G loss: -5.665775]
epoch32 step301545 [D loss: -0.861186] [G loss: -5.839493]
epoch32 step301550 [D loss: -0.009559] [G loss: -6.243279]
epoch32 step301555 [D loss: 0.766545] [G loss: -6.344718]
epoch32 step301560 [D loss: -0.560237] [G loss: -6.086802]
epo

epoch32 step302150 [D loss: -1.217395] [G loss: -5.133829]
epoch32 step302155 [D loss: -0.030150] [G loss: -5.309321]
epoch32 step302160 [D loss: -0.095468] [G loss: -5.863453]
epoch32 step302165 [D loss: -0.550723] [G loss: -5.037051]
epoch32 step302170 [D loss: -0.979310] [G loss: -4.758991]
epoch32 step302175 [D loss: -0.310160] [G loss: -4.829989]
epoch32 step302180 [D loss: -0.192671] [G loss: -5.607779]
epoch32 step302185 [D loss: -0.556317] [G loss: -4.833074]
epoch32 step302190 [D loss: -0.493393] [G loss: -5.032164]
epoch32 step302195 [D loss: -0.389820] [G loss: -4.749319]
epoch32 step302200 [D loss: 0.073084] [G loss: -4.688925]
##############
[2.68700569 2.07838953 1.69090253 3.29884459 0.69254427 5.75572649
 2.1850636  2.83595498 3.95207997 8.14868929]
##########
epoch32 step302205 [D loss: -0.333425] [G loss: -4.542882]
epoch32 step302210 [D loss: -1.071591] [G loss: -5.050655]
epoch32 step302215 [D loss: 0.515092] [G loss: -5.672090]
epoch32 step302220 [D loss: 0.692633]

KeyboardInterrupt: 